In [2]:
"""

영화 평점 데이터 기반으로 잠재 요인 협업 필터링 추천 시스템 설계
data load : https://grouplens.org/datasets/movielens/latest/

"""
!unzip ml-latest-small.zip

Archive:  ml-latest-small.zip
replace ml-latest-small/links.csv? [y]es, [n]o, [A]ll, [N]one, [r]ename: 

In [0]:
import pandas as pd
pd.options.display.max_rows=50
pd.options.display.max_columns=None
import numpy as np
from sklearn.metrics import mean_squared_error

In [0]:
def matrix_factorization(R, K, steps=200, learning_rate=0.01, r_lambda=0.01):
  num_users, num_items = R.shape
  # P와 Q 매트릭스의 크기를 지정하고 정규 분포를 가진 랜덤한 값으로 입력
  np.random.seed(1)
  P = np.random.normal(scale=1./K, size=(num_users, K))
  Q = np.random.normal(scale=1./K, size=(num_items, K))
  
  prev_rmse = 1000
  break_count = 0
  
  # R > 0인 행 위치, 열 위치, 값을 non_zeros 리스트 객체에 저장
  non_zeros = [(i,j,R[i,j]) for i in range(num_users) for j in range(num_items) if R[i, j] > 0]
  
  # SGD기법으로 P와 Q 매트릭스를 계속 업데이트
  for step in range(steps):
    for i, j, r in non_zeros:
      eij = r - np.dot(P[i, :], Q[j, :].T)
      # Regularaization을 반영한 SGD 업데이트 공식 적용
      P[i, :] = P[i, :] + learning_rate*(eij * Q[j, :] - r_lambda*P[i, :])
      Q[j, :] = Q[j, :] + learning_rate*(eij * P[i, :] - r_lambda*Q[j, :])
      
    rmse = get_rmse(R, P, Q, non_zeros)
    if (step % 10) == 0:
      print('### iteration step : ', step, 'rmse : ', rmse)
      
  return P, Q

In [0]:
def get_rmse(R, P, Q, non_zeros):
  error = 0
  full_pred_matrix = np.dot(P, Q.T)
  
  x_non_zero_ind = [non_zero[0] for non_zero in non_zeros]
  y_non_zero_ind = [non_zero[1] for non_zero in non_zeros]
  R_non_zeros = R[x_non_zero_ind, y_non_zero_ind]
  full_pred_matrix_non_zeros = full_pred_matrix[x_non_zero_ind, y_non_zero_ind]
  mse = mean_squared_error(R_non_zeros, full_pred_matrix_non_zeros)
  rmse = np.sqrt(mse)
  
  return rmse

In [0]:
def get_unseen_movies(ratings_matrix, userId):
  # userId로 입력 받은 사용자의 모든 영화 정보를 추출해 Series로 반환
  # 반환된 user_rating은 영화명(title)을 인덱스로 가지는 Series 객체
  user_rating = ratings_matrix.loc[userId, :]
  aleady_seen = user_rating[user_rating > 0].index.tolist()
  movies_list = ratings_matrix.columns.tolist()
  unseen_list = [movie for movie in movies_list if movie not in aleady_seen]
  return unseen_list

In [0]:
def recomm_movie_by_userid(pred_df, userId, unseen_list, top_n=10):
  recomm_movies = pred_df.loc[userId, unseen_list].sort_values(ascending=False)[:top_n]
  return recomm_movies

In [0]:
movies = pd.read_csv('./ml-latest-small/movies.csv')
ratings = pd.read_csv('./ml-latest-small/ratings.csv')
ratings = ratings[['userId', 'movieId', 'rating']]
ratings_matrix = ratings.pivot_table('rating', index='userId', columns='movieId')

In [0]:
ratings_movies = pd.merge(ratings, movies, on='movieId')
ratings_matrix = ratings_movies.pivot_table('rating', index='userId', columns='title')

In [10]:
P, Q = matrix_factorization(ratings_matrix.values, K=50, steps=200, learning_rate=0.01, r_lambda=0.01)

pred_matrix = np.dot(P, Q.T)

### iteration step :  0 rmse :  2.9023619751336867
### iteration step :  10 rmse :  0.7335768591017927
### iteration step :  20 rmse :  0.5115539026853442
### iteration step :  30 rmse :  0.37261628282537446
### iteration step :  40 rmse :  0.2960818299181014
### iteration step :  50 rmse :  0.2520353192341642
### iteration step :  60 rmse :  0.22487503275269854
### iteration step :  70 rmse :  0.2068545530233154
### iteration step :  80 rmse :  0.19413418783028685
### iteration step :  90 rmse :  0.18470082002720403
### iteration step :  100 rmse :  0.17742927527209104
### iteration step :  110 rmse :  0.17165226964707492
### iteration step :  120 rmse :  0.16695181946871723
### iteration step :  130 rmse :  0.16305292191997545
### iteration step :  140 rmse :  0.15976691929679646
### iteration step :  150 rmse :  0.1569598699945732
### iteration step :  160 rmse :  0.1545339818671543
### iteration step :  170 rmse :  0.15241618551077643
### iteration step :  180 rmse :  0.15055080739

In [11]:
ratings_pred_matrix = pd.DataFrame(data=pred_matrix, index=ratings_matrix.index, columns=ratings_matrix.columns)
ratings_pred_matrix.head(3)

title   '71 (2014)  'Hellboy': The Seeds of Creation (2004)  \
userId                                                        
1         3.055084                                 4.092018   
2         3.170119                                 3.657992   
3         2.307073                                 1.658853   

title   'Round Midnight (1986)  'Salem's Lot (2004)  \
userId                                                
1                     3.564130             4.502167   
2                     3.308707             4.166521   
3                     1.443538             2.208859   

title   'Til There Was You (1997)  'Tis the Season for Love (2015)  \
userId                                                               
1                        3.981215                         1.271694   
2                        4.311890                         1.275469   
3                        2.229486                         0.780760   

title   'burbs, The (1989)  'night Mother (1986)  (500) Days of Summer (2009)  \
userId                                                                          
1                 3.603274              2.333266                     5.091749   
2                 4.237972              1.900366                     3.392859   
3                 1.997043              0.924908                     2.970700   

title   *batteries not included (1987)  ...All the Marbles (1981)  \
userId                                                              
1                             3.972454                   1.623927   
2                             3.647421                   1.489588   
3                             2.551446                   0.881095   

title   ...And Justice for All (1979)  \
userId                                  
1                            3.910138   
2                            3.617857   
3                            1.813452   

title   00 Schneider - Jagd auf Nihil Baxter (1994)  1-900 (06) (1994)  \
userId                                                                   
1                                          4.775403           3.837260   
2                                          3.785199           3.168660   
3                                          2.687841           1.908641   

title   10 (1979)  10 Cent Pistol (2015)  10 Cloverfield Lane (2016)  \
userId                                                                 
1        3.875488               1.550801                    2.929129   
2        3.537318               0.995625                    3.969397   
3        2.228256               0.695248                    1.146590   

title   10 Items or Less (2006)  10 Things I Hate About You (1999)  \
userId                                                               
1                      2.680321                           3.225626   
2                      2.173005                           3.464055   
3                      1.536595                           0.809632   

title   10 Years (2011)  10,000 BC (2008)  100 Girls (2000)  \
userId                                                        
1              3.251925          2.778350          3.331543   
2              2.475622          3.413724          2.665215   
3              1.561342          1.820714          1.097596   

title   100 Streets (2016)  101 Dalmatians (1996)  \
userId                                              
1                 2.391855               3.199047   
2                 1.828840               3.322109   
3                 1.216409               1.347617   

title   101 Dalmatians (One Hundred and One Dalmatians) (1961)  \
userId                                                           
1                                                4.148949        
2                                                2.654698        
3                                                1.760926        

title   101 Dalmatians II: Patch's London Adventure (2003)  \
userId                                   

In [13]:
unseen_list = get_unseen_movies(ratings_matrix, 9)
recomm_movies = recomm_movie_by_userid(ratings_pred_matrix, 9, unseen_list, top_n=10)
recomm_movies = pd.DataFrame(data=recomm_movies.values, index=recomm_movies.index, columns=['pred_score'])
recomm_movies

pred_score
title                                                         
Rear Window (1954)                                    5.704612
South Park: Bigger, Longer and Uncut (1999)           5.451100
Rounders (1998)                                       5.298393
Blade Runner (1982)                                   5.244951
Roger & Me (1989)                                     5.191962
Gattaca (1997)                                        5.183179
Ben-Hur (1959)                                        5.130463
Rosencrantz and Guildenstern Are Dead (1990)          5.087375
Big Lebowski, The (1998)                              5.038690
Star Wars: Episode V - The Empire Strikes Back ...    4.989601